In [1]:
import os
import shutil
import cv2
import glob
import numpy 
import tensorflow as tf
import matplotlib.pyplot as plt
from collections import Counter
from sklearn.model_selection import train_test_split
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.preprocessing.image import ImageDataGenerator

2023-04-16 11:38:50.774100: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  SSE4.1 SSE4.2
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [2]:
keep_hmdb51 = ["clap", "climb", "drink", "jump", "pour", "ride_bike", "ride_horse", 
        "run", "shoot_bow", "smoke", "throw", "wave"]

TRAIN_TAG, TEST_TAG = 1, 2
train_files, test_files = [], []
train_labels, test_labels = [], []
split_pattern_name = f"*test_split1.txt"
split_pattern_path = os.path.join('HMDB51/test_train_splits', split_pattern_name)
annotation_paths = glob.glob(split_pattern_path)
for filepath in annotation_paths:
    class_name = '_'.join(filepath.split('/')[-1].split('_')[:-2])
    if class_name not in keep_hmdb51:
        continue  # skipping the classes that we won't use.
    with open(filepath) as fid:
        lines = fid.readlines()
    for line in lines:
        video_filename, tag_string = line.split()
        tag = int(tag_string)
        if tag == TRAIN_TAG:
            train_files.append(video_filename)
            train_labels.append(class_name)
        elif tag == TEST_TAG:
            test_files.append(video_filename)
            test_labels.append(class_name)

In [17]:
print(len(train_files))
print(train_labels)
print(len(test_files))
print(len(test_labels))

print(len(train_files)+len(test_files))

840
['throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'throw', 'ride_bike', 'ride_bike', 'ride_bike', 'ride_bike', 'ride_bike', 'ride_bike', 'ride_bike', 'ride_bike', 'ride_bike', 'ride_bike', 'ride_bike', 'ride_bike', 'ride_bike', 'ride_bike', 'ride_bike', 'ride_bike', 'ride_bike', 'ride_bike', 'ride_bike', 'ride_bike', 'ride_bike', 'ride_bike', 'ride_bike', 'ride_bike', 'ride_bike', 'ride_bike', 'ride_bike', 'ride_bike', '

In [3]:
#make list of all video paths
video_paths = []

for cls in keep_hmdb51:
    for video in os.listdir(f'HMDB51/video_data/{cls}'):
        if video.endswith('.avi'):
            video_paths.append(f'HMDB51/video_data/{cls}/{video}')

#print with id
for set_index, video_set in enumerate(video_paths):
    print(f'{set_index}:{video_set}')

0:HMDB51/video_data/clap/Finding_Forrester_3_clap_u_nm_np1_ri_med_0.avi
1:HMDB51/video_data/clap/LetThePeopleClap_clap_u_cm_np1_fr_med_3.avi
2:HMDB51/video_data/clap/#20_Rhythm_clap_u_nm_np1_le_goo_3.avi
3:HMDB51/video_data/clap/Faith_Rewarded_clap_u_cm_np1_ri_goo_1.avi
4:HMDB51/video_data/clap/LetThePeopleClap_clap_u_cm_np1_fr_med_2.avi
5:HMDB51/video_data/clap/Veoh_Alpha_Dog_1_clap_u_nm_np1_fr_goo_62.avi
6:HMDB51/video_data/clap/LetThePeopleClap_clap_u_cm_np1_fr_med_0.avi
7:HMDB51/video_data/clap/Aishwarya_Rai_Burns_David_Letterman_in_his_own_show_clap_u_cm_np1_fr_bad_1.avi
8:HMDB51/video_data/clap/LetThePeopleClap_clap_u_cm_np1_fr_med_1.avi
9:HMDB51/video_data/clap/Kurt_Kr_mer_-_Klatschen_im_Flugzeug_clap_u_cm_np1_fr_med_1.avi
10:HMDB51/video_data/clap/Song_I_Can_Wave_My_Hands_-_Cullen_s_Abc_s_clap_u_cm_np1_fr_med_3.avi
11:HMDB51/video_data/clap/NotAnotherTeenMovieslowclap_clap_u_cm_np1_fr_med_1.avi
12:HMDB51/video_data/clap/Hand_Clapping_Game__Bim_Bum__clap_f_nm_np2_fr_med_2.avi
13

In [4]:
maxsize=(170, 170)

# Lists to store the generated stacks and batches of optical flow frames alongside their corresponding actual frame
stacks_optical_flow_images = []

#for each video in either the training or the test set
for idx, video in enumerate(video_paths):
    #print(f'{idx}: {video}')

    if video.endswith("avi"): 
        video_file = video
        print(video_file)
        cap = cv2.VideoCapture(video_file)

        ret, frame1 = cap.read()
        print(ret)
        frame1 = numpy.array(cv2.resize(frame1, (maxsize[0], maxsize[1])))
        prvs = cv2.cvtColor(frame1, cv2.COLOR_BGR2GRAY)
        hsv = numpy.zeros_like(frame1)
        hsv[..., 1] = 255
        of_images = []

        while(1):
            ret, frame2 = cap.read()
            if not ret: break

            frame2 = numpy.array(cv2.resize(frame2, (maxsize[0], maxsize[1])))
            next = cv2.cvtColor(frame2, cv2.COLOR_BGR2GRAY)
            flow = cv2.calcOpticalFlowFarneback(prvs, next, None, 0.5, 3, 15, 3, 5, 1.2, 0)
            mag, ang = cv2.cartToPolar(flow[..., 0], flow[..., 1])
            hsv[..., 0] = ang*180/numpy.pi/2
            hsv[..., 2] = cv2.normalize(mag, None, 0, 255, cv2.NORM_MINMAX)
            bgr = cv2.cvtColor(hsv, cv2.COLOR_HSV2BGR)

            of_images.append(bgr)
            #print(len(of_images))
            prvs = next

    #========== END WHILE LOOP ================
            print(f'Next video, video nummer {idx}')
        middle_frame = len(of_images) // 2
        stacks_optical_flow_images.append(of_images[middle_frame])
        cv2.destroyAllWindows()

HMDB51/video_data/clap/Finding_Forrester_3_clap_u_nm_np1_ri_med_0.avi
True
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next video, video nummer 0
Next vi

Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
Next video, video nummer 1
N

Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
Next video, video nummer 4
N

Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
Next video, video nummer 6
N

Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
Next video, video nummer 8
N

...

Next video, video nummer 1521
Next video, video nummer 1521
Next video, video nummer 1521
Next video, video nummer 1521
Next video, video nummer 1521
Next video, video nummer 1521
Next video, video nummer 1521
Next video, video nummer 1521
Next video, video nummer 1521
Next video, video nummer 1521
Next video, video nummer 1521
Next video, video nummer 1521
Next video, video nummer 1521
Next video, video nummer 1521
Next video, video nummer 1521
Next video, video nummer 1521
Next video, video nummer 1521
Next video, video nummer 1521
Next video, video nummer 1521
Next video, video nummer 1521
Next video, video nummer 1521
Next video, video nummer 1521
Next video, video nummer 1521
HMDB51/video_data/wave/BIG_FISH_wave_u_nm_np1_fr_bad_4.avi
True
Next video, video nummer 1522
Next video, video nummer 1522
Next video, video nummer 1522
Next video, video nummer 1522
Next video, video nummer 1522
Next video, video nummer 1522
Next video, video nummer 1522
Next video, video nummer 1522
Next v

Next video, video nummer 1525
Next video, video nummer 1525
Next video, video nummer 1525
Next video, video nummer 1525
Next video, video nummer 1525
Next video, video nummer 1525
Next video, video nummer 1525
Next video, video nummer 1525
Next video, video nummer 1525
Next video, video nummer 1525
Next video, video nummer 1525
HMDB51/video_data/wave/50_FIRST_DATES_wave_u_cm_np1_fr_med_36.avi
True
Next video, video nummer 1526
Next video, video nummer 1526
Next video, video nummer 1526
Next video, video nummer 1526
Next video, video nummer 1526
Next video, video nummer 1526
Next video, video nummer 1526
Next video, video nummer 1526
Next video, video nummer 1526
Next video, video nummer 1526
Next video, video nummer 1526
Next video, video nummer 1526
Next video, video nummer 1526
Next video, video nummer 1526
Next video, video nummer 1526
Next video, video nummer 1526
Next video, video nummer 1526
Next video, video nummer 1526
Next video, video nummer 1526
Next video, video nummer 1526

Next video, video nummer 1529
Next video, video nummer 1529
Next video, video nummer 1529
HMDB51/video_data/wave/Miro_Klose_winkt_wave_f_cm_np1_le_med_0.avi
True
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 1530
Next video, video nummer 153

Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video, video nummer 1533
Next video

Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video, video nummer 1535
Next video

In [5]:
print(len(of_images))

52


In [9]:
print(len(stacks_optical_flow_images))

1537


In [10]:
print(stacks_optical_flow_images[10].shape)

#--> Input shape: 1537x170x170x3

(170, 170, 3)


In [8]:
stacks_optical_flow_images = numpy.array(stacks_optical_flow_images)
print(stacks_optical_flow_images.shape)

(1537, 170, 170, 3)


In [12]:
model = tf.keras.Sequential([
    tf.keras.layers.Conv2D(filters=32, kernel_size=3, padding='same', activation='relu', input_shape=(170, 170, 3)),
    tf.keras.layers.MaxPooling2D(pool_size=2),
    tf.keras.layers.Conv2D(filters=64, kernel_size=3, padding='same', activation='relu'),
    tf.keras.layers.MaxPooling2D(pool_size=2),
    tf.keras.layers.Conv2D(filters=128, kernel_size=3, padding='same', activation='relu'),
    tf.keras.layers.MaxPooling2D(pool_size=2),
    tf.keras.layers.Conv2D(filters=256, kernel_size=3, padding='same', activation='relu'),
    tf.keras.layers.MaxPooling2D(pool_size=2),
    tf.keras.layers.Flatten(),
    tf.keras.layers.Dense(units=1024, activation='relu'),
    tf.keras.layers.Dropout(0.5),
    tf.keras.layers.Dense(units=12, activation='softmax')
])

model.compile(optimizer='adam', loss='sparse_categorical_crossentropy', metrics=['accuracy'])

In [ ]:
no_clr_history = model.fit(x_train, y_train, epochs=10, batch_size=32)

## 3d convolve

In [11]:
model = tf.keras.Sequential([
    tf.keras.layers.Conv3D(filters=32, kernel_size=(3, 3, 3), padding='same', activation='relu', input_shape=(170, 170, 3)),
    tf.keras.layers.MaxPooling3D(pool_size=(2, 2, 2)),
    tf.keras.layers.Conv3D(filters=64, kernel_size=(3, 3, 3), padding='same', activation='relu'),
    tf.keras.layers.MaxPooling3D(pool_size=(2, 2, 2)),
    tf.keras.layers.Conv3D(filters=128, kernel_size=(3, 3, 3), padding='same', activation='relu'),
    tf.keras.layers.MaxPooling3D(pool_size=(2, 2, 2)),
    tf.keras.layers.Flatten(),
    tf.keras.layers.Dense(units=512, activation='relu'),
    tf.keras.layers.Dropout(0.5),
    tf.keras.layers.Dense(units=12, activation='softmax')
])

model.compile(optimizer='adam', loss='sparse_categorical_crossentropy', metrics=['accuracy'])


ValueError: Input 0 of layer "conv3d" is incompatible with the layer: expected min_ndim=5, found ndim=4. Full shape received: (None, 170, 170, 3)

In [20]:
import cv2
import os

# define parameters for optical flow calculation
pyr_scale = 0.5
levels = 3
winsize = 15
iterations = 3
poly_n = 5
poly_sigma = 1.2
flags = 0

# define path to directory containing video files
video_dir = f'HMDB51/video_data/clap'

# loop over all video files in directory
for filename in os.listdir(video_dir):
    if not filename.endswith('.avi'):
        continue
    
    # open video file
    filepath = os.path.join(video_dir, filename)
    cap = cv2.VideoCapture(filepath)
    
    # create output directory for optical flow frames
    output_dir = os.path.join(video_dir, f'{filename}_optical_flow_frames')
    os.makedirs(output_dir, exist_ok=True)
    
    # read first frame
    ret, frame1 = cap.read()
    prvs = cv2.cvtColor(frame1, cv2.COLOR_BGR2GRAY)
    
    # loop through video frames and calculate optical flow
    while True:
        ret, frame2 = cap.read()
        if not ret:
            break
        
        # convert current frame to grayscale
        next = cv2.cvtColor(frame2, cv2.COLOR_BGR2GRAY)
        
        # calculate optical flow using Farneback method
        flow = cv2.calcOpticalFlowFarneback(prvs, next, None, pyr_scale, levels, winsize, iterations, poly_n, poly_sigma, flags)
        
        # save optical flow image
        flow_image = cv2.cvtColor(flow, cv2.COLOR_BGR2GRAY)
        frame_num = int(cap.get(cv2.CAP_PROP_POS_FRAMES))
        output_path = os.path.join(output_dir, f'frame_{frame_num:06d}.png')
        cv2.imwrite(output_path, flow_image)
        
        # set previous frame for next iteration
        prvs = next
    
    # release video file handle
    cap.release()

error: OpenCV(4.7.0) /Users/runner/work/opencv-python/opencv-python/opencv/modules/imgproc/src/color.simd_helpers.hpp:92: error: (-2:Unspecified error) in function 'cv::impl::(anonymous namespace)::CvtHelper<cv::impl::(anonymous namespace)::Set<3, 4, -1>, cv::impl::(anonymous namespace)::Set<1, -1, -1>, cv::impl::(anonymous namespace)::Set<0, 2, 5>, cv::impl::(anonymous namespace)::NONE>::CvtHelper(cv::InputArray, cv::OutputArray, int) [VScn = cv::impl::(anonymous namespace)::Set<3, 4, -1>, VDcn = cv::impl::(anonymous namespace)::Set<1, -1, -1>, VDepth = cv::impl::(anonymous namespace)::Set<0, 2, 5>, sizePolicy = cv::impl::(anonymous namespace)::NONE]'
> Invalid number of channels in input image:
>     'VScn::contains(scn)'
> where
>     'scn' is 2


In [45]:
import cv2
import os

# define parameters for optical flow calculation
pyr_scale = 0.5
levels = 3
winsize = 15
iterations = 3
poly_n = 5
poly_sigma = 1.2
flags = 0

# define paths to videos
video_paths = video_paths

# define time points for optical flow calculation
time_points = [1, 3, 5, 7, 9, 11, 13, 15, 17, 19, 21, 23, 25, 27, 29, 31]

for video_path in video_paths:
    # create output directory for optical flow frames
    output_dir = os.path.join(os.path.dirname(video_path), 'optical_flow_frames')
    os.makedirs(output_dir, exist_ok=True)
    
    # open video file
    cap = cv2.VideoCapture(video_path)
    
    # read first frame
    ret, frame1 = cap.read()
    print(frame1.shape)
    prvs = cv2.cvtColor(frame1, cv2.COLOR_BGR2GRAY)
    print(prvs.shape)
    
    # loop through time points and calculate optical flow
    for t in time_points:
        # calculate frame number at time t
        frame_num = int(t * cap.get(cv2.CAP_PROP_FPS))
        
        # set video file position to frame_num
        cap.set(cv2.CAP_PROP_POS_FRAMES, frame_num)
        
        # read frame at frame_num
        ret, frame2 = cap.read()
        if not ret:
            break
        
        # convert frames to grayscale
        print(frame2.shape)
        next = cv2.cvtColor(frame2, cv2.COLOR_BGR2GRAY)
        print(next.shape)
        
        # calculate optical flow using Farneback method
        flow = cv2.calcOpticalFlowFarneback(prvs, next, None, pyr_scale, levels, winsize, iterations, poly_n, poly_sigma, flags)
        
        # save optical flow image
        flow_image = cv2.cvtColor(flow, cv2.COLOR_BGR2GRAY)
        output_path = os.path.join(output_dir, f't_{t:02d}.png')
        cv2.imwrite(output_path, flow_image)
        
        # set previous frame for next iteration
        prvs = next
    
    # release video file handle
    cap.release()

(240, 352, 3)
(240, 352)
(240, 352, 3)
(240, 352)


error: OpenCV(4.7.0) /Users/runner/work/opencv-python/opencv-python/opencv/modules/imgproc/src/color.simd_helpers.hpp:92: error: (-2:Unspecified error) in function 'cv::impl::(anonymous namespace)::CvtHelper<cv::impl::(anonymous namespace)::Set<3, 4, -1>, cv::impl::(anonymous namespace)::Set<1, -1, -1>, cv::impl::(anonymous namespace)::Set<0, 2, 5>, cv::impl::(anonymous namespace)::NONE>::CvtHelper(cv::InputArray, cv::OutputArray, int) [VScn = cv::impl::(anonymous namespace)::Set<3, 4, -1>, VDcn = cv::impl::(anonymous namespace)::Set<1, -1, -1>, VDepth = cv::impl::(anonymous namespace)::Set<0, 2, 5>, sizePolicy = cv::impl::(anonymous namespace)::NONE]'
> Invalid number of channels in input image:
>     'VScn::contains(scn)'
> where
>     'scn' is 2
